# Baseball - Predicting players' salary

*NOTE: Due to featuretools' memory requirement, this notebook will not run on MyBinder.*

In this notebook, we will benchmark several of getML's feature learning algorithms against featuretools using a dataset related to baseball players' salary.

Summary:

- Prediction type: __Regression model__
- Domain: __Sports__
- Prediction target: __Salaries__ 
- Population size: __23111__

_Author: Dr. Patrick Urbanke_

# Background

In the late 1990s, the Oakland Athletics began focusing on the idea of *sabermetrics*, using statistical methods to identify undervalued baseball players. This was done to compensate for the fact that the team had a significantly smaller budget than most other teams in its league. Under its general manager Billy Beane, the Oakland Athletics became the first team in over 100 years to win 20 consecutive games in a row, despite still being significantly disadvantaged in terms of its budget. After this remarkable success, the use of sabermetrics quickly became the norm in baseball. These events have been documented in a bestselling book and a movie, both called *Moneyball*. 

In this notebook, we will demonstrate that relational learning can be used for sabermetrics. Specifically, we will develop a model to predict players' salary using getML's statistical relational learning algorithms. Such predictions can then be used to identify undervalued players. 

The dataset has been downloaded from the [CTU Prague relational learning repository](https://relational.fit.cvut.cz/dataset/Lahman) (Motl and Schulte, 2015).

We will benchmark [getML](https://www.getml.com) 's feature learning algorithms against [featuretools](https://www.featuretools.com), an open-source implementation of the propositionalization algorithm, similar to getML's FastProp.

### A web frontend for getML

The getML monitor is a frontend built to support your work with getML. The getML monitor displays information such as the imported data frames, trained pipelines and allows easy data and feature exploration. You can launch the getML monitor [here](http://localhost:1709).

### Where is this running?

Your getML live session is running inside a docker container on [mybinder.org](https://mybinder.org/), a service built by the Jupyter community and funded by Google Cloud, OVH, GESIS Notebooks and the Turing Institute. As it is a free service, this session will shut down after 10 minutes of inactivity.

# Analysis

Let's get started with the analysis and set up your session:

In [1]:
import copy
import os
from urllib import request

import numpy as np
import pandas as pd
from IPython.display import Image
import matplotlib.pyplot as plt
plt.style.use('seaborn')
%matplotlib inline  

import featuretools
import getml

getml.engine.set_project('baseball')




Connected to project 'baseball'


## 1. Loading data

### 1.1 Download from source

We begin by downloading the data:

In [2]:
conn = getml.database.connect_mariadb(
    host="relational.fit.cvut.cz",
    dbname="lahman_2014",
    port=3306,
    user="guest",
    password="relational"
)

conn

Connection(conn_id='default',
           dbname='lahman_2014',
           dialect='mysql',
           host='relational.fit.cvut.cz',
           port=3306)

In [3]:
def load_if_needed(name):
    """
    Loads the data from the relational learning
    repository, if the data frame has not already
    been loaded.
    """
    if not getml.data.exists(name):
        data_frame = getml.data.DataFrame.from_db(
            name=name,
            table_name=name,
            conn=conn
        )
        data_frame.save()
    else:
        data_frame = getml.data.load_data_frame(name)
    return data_frame

In [4]:
allstarfull = load_if_needed("allstarfull")
awardsplayers = load_if_needed("awardsplayers")
awardsshareplayers = load_if_needed("awardsshareplayers")
batting = load_if_needed("batting")
battingpost = load_if_needed("battingpost")
fielding = load_if_needed("fielding")
fieldingpost = load_if_needed("fieldingpost")
pitching = load_if_needed("pitching")
pitchingpost = load_if_needed("pitchingpost")
salaries = load_if_needed("salaries")

In [5]:
allstarfull

name         yearID        gameNum             GP    startingPos   playerID        gameID          teamID       
role   unused_float   unused_float   unused_float   unused_float   unused_string   unused_string   unused_string
   0           1955              0              1           nan    aaronha01       NLS195507120    ML1          
   1           1956              0              1           nan    aaronha01       ALS195607100    ML1          
   2           1957              0              1             9    aaronha01       NLS195707090    ML1          
   3           1958              0              1             9    aaronha01       ALS195807080    ML1          
   4           1959              1              1             9    aaronha01       NLS195907070    ML1          
                ...            ...            ...            ...   ...             ...             ...          
4826           1978              0              1             9    ziskri01        NLS197807110    TEX          
4827           2002              0              1           nan    zitoba01        NLS200207090    OAK          
4828           2003              0              0           nan    zitoba01        ALS200307150    OAK          
4829           2006              0              1           nan    zitoba01        NLS200607110    OAK          
4830           2009              0              1           nan    zobribe01       NLS200907140    TBA          

name   lgID         
role   unused_string
   0   NL           
   1   NL           
   2   NL           
   3   NL           
   4   NL           
       ...          
4826   AL           
4827   AL           
4828   AL           
4829   AL           
4830   AL           


4831 rows x 8 columns
memory usage: 0.45 MB
name: allstarfull
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/allstarfull/

In [6]:
awardsplayers

name         yearID   playerID        awardID                            lgID            tie             notes        
role   unused_float   unused_string   unused_string                      unused_string   unused_string   unused_string
   0           1877   bondto01        Pitching Triple Crown              NL              NULL            NULL         
   1           1878   hinespa01       Triple Crown                       NL              NULL            NULL         
   2           1884   heckegu01       Pitching Triple Crown              AA              NULL            NULL         
   3           1884   radboch01       Pitching Triple Crown              NL              NULL            NULL         
   4           1887   oneilti01       Triple Crown                       AA              NULL            NULL         
                ...   ...             ...                                ...             ...             ...          
5790           2012   larocad01       Silver Slugger                     NL              NULL            1B           
5791           2012   cabremi01       Triple Crown                       NL              NULL            NULL         
5792           2012   cabremi01       TSN Major League Player of the Y...   ML              NULL            NULL         
5793           2012   verlaju01       TSN Pitcher of the Year            AL              Y               NULL         
5794           2012   dickera01       TSN Pitcher of the Year            NL              NULL            NULL         


5795 rows x 6 columns
memory usage: 0.51 MB
name: awardsplayers
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/awardsplayers/

In [7]:
awardsshareplayers

name         yearID      pointsWon      pointsMax     votesFirst   awardID              lgID            playerID     
role   unused_float   unused_float   unused_float   unused_float   unused_string        unused_string   unused_string
   0           1956              1             16              1   Cy Young             ML              fordwh01     
   1           1956              4             16              4   Cy Young             ML              maglisa01    
   2           1956             10             16             10   Cy Young             ML              newcodo01    
   3           1956              1             16              1   Cy Young             ML              spahnwa01    
   4           1957              1             16              1   Cy Young             ML              donovdi01    
                ...            ...            ...            ...   ...                  ...             ...          
6284           2006              1            160              0   Rookie of the Year   NL              willijo03    
6285           2006            101            160             10   Rookie of the Year   NL              zimmery01    
6286           2008              3            140              0   Rookie of the Year   AL              devinjo01    
6287           2008            158            160             31   Rookie of the Year   NL              sotoge01     
6288           2008              9            160              0   Rookie of the Year   NL              volqued01    


6289 rows x 7 columns
memory usage: 0.47 MB
name: awardsshareplayers
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/awardsshareplayers/

In [8]:
batting

name         yearID          stint              G      G_batting   ...           GIDP          G_old   playerID     
 role   unused_float   unused_float   unused_float   unused_float   ...   unused_float   unused_float   unused_string
    0           2004              1             11             11   ...             0             11    aardsda01    
    1           2006              1             45             43   ...             0             45    aardsda01    
    2           2007              1             25              2   ...             0              2    aardsda01    
    3           2008              1             47              5   ...             0              5    aardsda01    
    4           2009              1             73              3   ...             0            nan    aardsda01    
                 ...            ...            ...            ...                  ...            ...   ...          
92348           1959              1              6              6   ...             0              6    zuverge01    
92349           1910              1             27             27   ...           nan             27    zwilldu01    
92350           1914              1            154            154   ...           nan            154    zwilldu01    
92351           1915              1            150            150   ...           nan            150    zwilldu01    
92352           1916              1             35             35   ...           nan             35    zwilldu01    

 name   teamID          lgID         
 role   unused_string   unused_string
    0   SFN             NL           
    1   CHN             NL           
    2   CHA             AL           
    3   BOS             AL           
    4   SEA             AL           
        ...             ...          
92348   BAL             AL           
92349   CHA             AL           
92350   CHF             FL           
92351   CHF             FL           
92352   CHN             NL           


92353 rows x 24 columns
memory usage: 19.29 MB
name: batting
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/batting/

In [9]:
battingpost

name         yearID              G             AB              R   ...           GIDP   round           playerID     
role   unused_float   unused_float   unused_float   unused_float   ...   unused_float   unused_string   unused_string
   0           1884              1              2              0   ...           nan    WS              becanbu01    
   1           1884              3             10              1   ...           nan    WS              bradyst01    
   2           1884              3             10              2   ...           nan    WS              carrocl01    
   3           1884              3              9              3   ...           nan    WS              dennyje01    
   4           1884              3             10              0   ...           nan    WS              esterdu01    
                ...            ...            ...            ...                  ...   ...             ...          
9793           2012              2              5              1   ...           nan    WS              theriry01    
9794           2012              1              0              0   ...           nan    WS              valvejo01    
9795           2012              1              1              0   ...           nan    WS              verlaju01    
9796           2012              1              0              0   ...           nan    WS              vogelry01    
9797           2012              1              2              0   ...           nan    WS              zitoba01     

name   teamID          lgID         
role   unused_string   unused_string
   0   NY4             AA           
   1   NY4             AA           
   2   PRO             NL           
   3   PRO             NL           
   4   NY4             AA           
       ...             ...          
9793   SFN             NL           
9794   DET             AL           
9795   DET             AL           
9796   SFN             NL           
9797   SFN             NL           


9798 rows x 22 columns
memory usage: 1.93 MB
name: battingpost
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/battingpost/

In [10]:
fielding

name         yearID          stint              G             GS   ...             ZR   playerID        teamID       
  role   unused_float   unused_float   unused_float   unused_float   ...   unused_float   unused_string   unused_string
     0           2004              1             11             0    ...           nan    aardsda01       SFN          
     1           2006              1             45             0    ...           nan    aardsda01       CHN          
     2           2007              1             25             0    ...           nan    aardsda01       CHA          
     3           2008              1             47             0    ...           nan    aardsda01       BOS          
     4           2009              1             73             0    ...           nan    aardsda01       SEA          
                  ...            ...            ...            ...                  ...   ...             ...          
137970           1910              1             27           nan    ...           nan    zwilldu01       CHA          
137971           1914              1            154           nan    ...           nan    zwilldu01       CHF          
137972           1915              1              3           nan    ...           nan    zwilldu01       CHF          
137973           1915              1            148           nan    ...           nan    zwilldu01       CHF          
137974           1916              1             10           nan    ...           nan    zwilldu01       CHN          

  name   lgID            POS          
  role   unused_string   unused_string
     0   NL              P            
     1   NL              P            
     2   AL              P            
     3   AL              P            
     4   AL              P            
         ...             ...          
137970   AL              OF           
137971   FL              OF           
137972   FL              1B           
137973   FL              OF           
137974   NL              OF           


137975 rows x 18 columns
memory usage: 22.57 MB
name: fielding
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/fielding/

In [11]:
fieldingpost

name         yearID              G             GS        InnOuts   ...   playerID        teamID          lgID         
 role   unused_float   unused_float   unused_float   unused_float   ...   unused_string   unused_string   unused_string
    0           1957              7              7            186   ...   aaronha01       ML1             NL           
    1           1958              1              1             21   ...   aaronha01       ML1             NL           
    2           1958              7              6            168   ...   aaronha01       ML1             NL           
    3           1969              3              3             78   ...   aaronha01       ATL             NL           
    4           1979              2              0             15   ...   aasedo01        CAL             AL           
                 ...            ...            ...            ...         ...             ...             ...          
10341           2006              1              1             24   ...   zitoba01        OAK             AL           
10342           2012              1              1             23   ...   zitoba01        SFN             NL           
10343           2012              1              1              8   ...   zitoba01        SFN             NL           
10344           2012              1              1             17   ...   zitoba01        SFN             NL           
10345           1946              1              0              6   ...   zuberbi01       BOS             AL           

 name   round           POS          
 role   unused_string   unused_string
    0   WS              CF           
    1   WS              CF           
    2   WS              RF           
    3   NLCS            RF           
    4   ALCS            P            
        ...             ...          
10341   ALDS2           P            
10342   NLCS            P            
10343   NLDS2           P            
10344   WS              P            
10345   WS              P            


10346 rows x 17 columns
memory usage: 1.65 MB
name: fieldingpost
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/fieldingpost/

In [12]:
pitching

name         yearID          stint              W              L   ...             SF           GIDP   playerID     
 role   unused_float   unused_float   unused_float   unused_float   ...   unused_float   unused_float   unused_string
    0           2004              1              1              0   ...           nan            nan    aardsda01    
    1           2006              1              3              0   ...           nan            nan    aardsda01    
    2           2007              1              2              1   ...           nan            nan    aardsda01    
    3           2008              1              4              2   ...           nan            nan    aardsda01    
    4           2009              1              3              6   ...           nan            nan    aardsda01    
                 ...            ...            ...            ...                  ...            ...   ...          
39356           1955              2              4              3   ...           nan            nan    zuverge01    
39357           1956              1              7              6   ...           nan            nan    zuverge01    
39358           1957              1             10              6   ...           nan            nan    zuverge01    
39359           1958              1              2              2   ...           nan            nan    zuverge01    
39360           1959              1              0              1   ...           nan            nan    zuverge01    

 name   teamID          lgID         
 role   unused_string   unused_string
    0   SFN             NL           
    1   CHN             NL           
    2   CHA             AL           
    3   BOS             AL           
    4   SEA             AL           
        ...             ...          
39356   BAL             AL           
39357   BAL             AL           
39358   BAL             AL           
39359   BAL             AL           
39360   BAL             AL           


39361 rows x 30 columns
memory usage: 10.11 MB
name: pitching
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/pitching/

In [13]:
pitchingpost

name         yearID              W              L              G   ...           GIDP   playerID        round        
role   unused_float   unused_float   unused_float   unused_float   ...   unused_float   unused_string   unused_string
   0           1979              1              0              2   ...              0   aasedo01        ALCS         
   1           1975              0              0              1   ...              0   abbotgl01       ALCS         
   2           2000              0              1              1   ...              0   abbotpa01       ALCS         
   3           2000              1              0              1   ...              1   abbotpa01       ALDS2        
   4           2001              0              0              1   ...              0   abbotpa01       ALCS         
                ...            ...            ...            ...                  ...   ...             ...          
4192           2006              1              0              1   ...              0   zitoba01        ALDS2        
4193           2012              1              0              1   ...              1   zitoba01        NLCS         
4194           2012              0              0              1   ...              0   zitoba01        NLDS2        
4195           2012              1              0              1   ...              1   zitoba01        WS           
4196           1946              0              0              1   ...              1   zuberbi01       WS           

name   teamID          lgID         
role   unused_string   unused_string
   0   CAL             AL           
   1   OAK             AL           
   2   SEA             AL           
   3   SEA             AL           
   4   SEA             AL           
       ...             ...          
4192   OAK             AL           
4193   SFN             NL           
4194   SFN             NL           
4195   SFN             NL           
4196   BOS             AL           


4197 rows x 30 columns
memory usage: 1.10 MB
name: pitchingpost
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/pitchingpost/

In [14]:
salaries

name         yearID         salary   teamID          lgID            playerID     
 role   unused_float   unused_float   unused_string   unused_string   unused_string
    0           1985         870000   ATL             NL              barkele01    
    1           1985         550000   ATL             NL              bedrost01    
    2           1985         545000   ATL             NL              benedbr01    
    3           1985         633333   ATL             NL              campri01     
    4           1985         625000   ATL             NL              ceronri01    
                 ...            ...   ...             ...             ...          
23106           2012         750000   WAS             NL              tracych01    
23107           2012        4000000   WAS             NL              wangch01     
23108           2012       13571428   WAS             NL              werthja01    
23109           2012        2300000   WAS             NL              zimmejo02    
23110           2012       12000000   WAS             NL              zimmery01    


23111 rows x 5 columns
memory usage: 1.31 MB
name: salaries
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/salaries/

### 1.2 Prepare data for getML

getML requires that we define *roles* for each of the columns.

In [15]:
allstarfull["year"] = allstarfull["yearID"].as_str().as_ts(["%Y"])

allstarfull.set_role(["playerID"], getml.data.roles.join_key)
allstarfull.set_role(allstarfull.roles.unused_string, getml.data.roles.categorical)
allstarfull.set_role(allstarfull.roles.unused_float, getml.data.roles.numerical)
allstarfull.set_role("year", getml.data.roles.time_stamp)

allstarfull.set_role("yearID", getml.data.roles.unused_float)

allstarfull

name                          year    playerID   gameID         teamID        lgID            gameNum          GP
role                    time_stamp    join_key   categorical    categorical   categorical   numerical   numerical
unit   time stamp, comparison only                                                                               
   0                    1955-01-01   aaronha01   NLS195507120   ML1           NL                    0           1
   1                    1956-01-01   aaronha01   ALS195607100   ML1           NL                    0           1
   2                    1957-01-01   aaronha01   NLS195707090   ML1           NL                    0           1
   3                    1958-01-01   aaronha01   ALS195807080   ML1           NL                    0           1
   4                    1959-01-01   aaronha01   NLS195907070   ML1           NL                    1           1
                               ...         ...   ...            ...           ...                 ...         ...
4826                    1978-01-01    ziskri01   NLS197807110   TEX           AL                    0           1
4827                    2002-01-01    zitoba01   NLS200207090   OAK           AL                    0           1
4828                    2003-01-01    zitoba01   ALS200307150   OAK           AL                    0           0
4829                    2006-01-01    zitoba01   NLS200607110   OAK           AL                    0           1
4830                    2009-01-01   zobribe01   NLS200907140   TBA           AL                    0           1

name   startingPos         yearID
role     numerical   unused_float
unit                             
   0          nan            1955
   1          nan            1956
   2            9            1957
   3            9            1958
   4            9            1959
               ...            ...
4826            9            1978
4827          nan            2002
4828          nan            2003
4829          nan            2006
4830          nan            2009


4831 rows x 9 columns
memory usage: 0.27 MB
name: allstarfull
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/allstarfull/

In [16]:
awardsplayers["year"] = awardsplayers["yearID"].as_str().as_ts(["%Y"])

awardsplayers.set_role(["playerID"], getml.data.roles.join_key)
awardsplayers.set_role(["awardID", "lgID", "notes"], getml.data.roles.categorical)
awardsplayers.set_role("year", getml.data.roles.time_stamp)

awardsplayers

name                          year    playerID   awardID                            lgID          notes               yearID
role                    time_stamp    join_key   categorical                        categorical   categorical   unused_float
unit   time stamp, comparison only                                                                                          
   0                    1877-01-01    bondto01   Pitching Triple Crown              NL            NULL                  1877
   1                    1878-01-01   hinespa01   Triple Crown                       NL            NULL                  1878
   2                    1884-01-01   heckegu01   Pitching Triple Crown              AA            NULL                  1884
   3                    1884-01-01   radboch01   Pitching Triple Crown              NL            NULL                  1884
   4                    1887-01-01   oneilti01   Triple Crown                       AA            NULL                  1887
                               ...         ...   ...                                ...           ...                    ...
5790                    2012-01-01   larocad01   Silver Slugger                     NL            1B                    2012
5791                    2012-01-01   cabremi01   Triple Crown                       NL            NULL                  2012
5792                    2012-01-01   cabremi01   TSN Major League Player of the Y...   ML            NULL       
5793                    2012-01-01   verlaju01   TSN Pitcher of the Year            AL            NULL                  2012
5794                    2012-01-01   dickera01   TSN Pitcher of the Year            NL            NULL                  2012

name   tie          
role   unused_string
unit                
   0   NULL         
   1   NULL         
   2   NULL         
   3   NULL         
   4   NULL         
       ...          
5790   NULL         
5791   NULL         
5792           2012   NULL         
5793   Y            
5794   NULL         


5795 rows x 7 columns
memory usage: 0.26 MB
name: awardsplayers
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/awardsplayers/

In [17]:
awardsshareplayers["year"] = awardsshareplayers["yearID"].as_str().as_ts(["%Y"])

awardsshareplayers.set_role(["playerID"], getml.data.roles.join_key)
awardsshareplayers.set_role(awardsshareplayers.roles.unused_float, getml.data.roles.numerical)
awardsshareplayers.set_role(awardsshareplayers.roles.unused_string, getml.data.roles.categorical)
awardsshareplayers.set_role("yearID", getml.data.roles.unused_float)
awardsshareplayers.set_role("year", getml.data.roles.time_stamp)

awardsshareplayers

name                          year    playerID   awardID              lgID          pointsWon   pointsMax   votesFirst
role                    time_stamp    join_key   categorical          categorical   numerical   numerical    numerical
unit   time stamp, comparison only                                                                                    
   0                    1956-01-01    fordwh01   Cy Young             ML                    1          16            1
   1                    1956-01-01   maglisa01   Cy Young             ML                    4          16            4
   2                    1956-01-01   newcodo01   Cy Young             ML                   10          16           10
   3                    1956-01-01   spahnwa01   Cy Young             ML                    1          16            1
   4                    1957-01-01   donovdi01   Cy Young             ML                    1          16            1
                               ...         ...   ...                  ...                 ...         ...          ...
6284                    2006-01-01   willijo03   Rookie of the Year   NL                    1         160            0
6285                    2006-01-01   zimmery01   Rookie of the Year   NL                  101         160           10
6286                    2008-01-01   devinjo01   Rookie of the Year   AL                    3         140            0
6287                    2008-01-01    sotoge01   Rookie of the Year   NL                  158         160           31
6288                    2008-01-01   volqued01   Rookie of the Year   NL                    9         160            0

name         yearID
role   unused_float
unit               
   0           1956
   1           1956
   2           1956
   3           1956
   4           1957
                ...
6284           2006
6285           2006
6286           2008
6287           2008
6288           2008


6289 rows x 8 columns
memory usage: 0.33 MB
name: awardsshareplayers
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/awardsshareplayers/

In [18]:
batting["year"] = batting["yearID"].as_str().as_ts(["%Y"])

batting.set_role(["playerID", "teamID"], getml.data.roles.join_key)
batting.set_role(batting.roles.unused_float, getml.data.roles.numerical)
batting.set_role(batting.roles.unused_string, getml.data.roles.categorical)
batting.set_role("yearID", getml.data.roles.unused_float)
batting.set_role("year", getml.data.roles.time_stamp)

batting

name                          year    playerID     teamID   lgID          ...          SH          SF        GIDP       G_old
 role                    time_stamp    join_key   join_key   categorical   ...   numerical   numerical   numerical   numerical
 unit   time stamp, comparison only                                        ...                                                
    0                    2004-01-01   aardsda01        SFN   NL            ...           0          0           0          11 
    1                    2006-01-01   aardsda01        CHN   NL            ...           1          0           0          45 
    2                    2007-01-01   aardsda01        CHA   AL            ...           0          0           0           2 
    3                    2008-01-01   aardsda01        BOS   AL            ...           0          0           0           5 
    4                    2009-01-01   aardsda01        SEA   AL            ...           0          0           0         nan 
                                ...         ...        ...   ...                       ...         ...         ...         ...
92348                    1959-01-01   zuverge01        BAL   AL            ...           0          0           0           6 
92349                    1910-01-01   zwilldu01        CHA   AL            ...           1        nan         nan          27 
92350                    1914-01-01   zwilldu01        CHF   FL            ...          10        nan         nan         154 
92351                    1915-01-01   zwilldu01        CHF   FL            ...          18        nan         nan         150 
92352                    1916-01-01   zwilldu01        CHN   NL            ...           2        nan         nan          35 

 name         yearID
 role   unused_float
 unit               
    0           2004
    1           2006
    2           2007
    3           2008
    4           2009
                 ...
92348           1959
92349           1910
92350           1914
92351           1915
92352           1916


92353 rows x 25 columns
memory usage: 17.36 MB
name: batting
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/batting/

In [19]:
battingpost["year"] = battingpost["yearID"].as_str().as_ts(["%Y"])

battingpost.set_role(["playerID", "teamID"], getml.data.roles.join_key)
battingpost.set_role(battingpost.roles.unused_float, getml.data.roles.numerical)
battingpost.set_role(battingpost.roles.unused_string, getml.data.roles.categorical)
battingpost.set_role("yearID", getml.data.roles.unused_float)
battingpost.set_role("year", getml.data.roles.time_stamp)

battingpost

name                          year    playerID     teamID   round         ...         HBP          SH          SF        GIDP
role                    time_stamp    join_key   join_key   categorical   ...   numerical   numerical   numerical   numerical
unit   time stamp, comparison only                                        ...                                                
   0                    1884-01-01   becanbu01        NY4   WS            ...        nan         nan         nan         nan 
   1                    1884-01-01   bradyst01        NY4   WS            ...        nan         nan         nan         nan 
   2                    1884-01-01   carrocl01        PRO   WS            ...        nan         nan         nan         nan 
   3                    1884-01-01   dennyje01        PRO   WS            ...        nan         nan         nan         nan 
   4                    1884-01-01   esterdu01        NY4   WS            ...        nan         nan         nan         nan 
                               ...         ...        ...   ...                       ...         ...         ...         ...
9793                    2012-01-01   theriry01        SFN   WS            ...        nan         nan         nan         nan 
9794                    2012-01-01   valvejo01        DET   WS            ...        nan         nan         nan         nan 
9795                    2012-01-01   verlaju01        DET   WS            ...        nan         nan         nan         nan 
9796                    2012-01-01   vogelry01        SFN   WS            ...        nan         nan         nan         nan 
9797                    2012-01-01    zitoba01        SFN   WS            ...        nan         nan         nan         nan 

name         yearID
role   unused_float
unit               
   0           1884
   1           1884
   2           1884
   3           1884
   4           1884
                ...
9793           2012
9794           2012
9795           2012
9796           2012
9797           2012


9798 rows x 23 columns
memory usage: 1.65 MB
name: battingpost
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/battingpost/

In [20]:
fielding["year"] = fielding["yearID"].as_str().as_ts(["%Y"])

fielding.set_role(["playerID", "teamID"], getml.data.roles.join_key)
fielding.set_role(["stint", "G","GS","InnOuts", "PO", "A", "E", "DP"], getml.data.roles.numerical)
fielding.set_role(fielding.roles.unused_string, getml.data.roles.categorical)
fielding.set_role("year", getml.data.roles.time_stamp)

fielding

name                          year    playerID     teamID   lgID          ...             PB             WP             SB
  role                    time_stamp    join_key   join_key   categorical   ...   unused_float   unused_float   unused_float
  unit   time stamp, comparison only                                        ...                                             
     0                    2004-01-01   aardsda01        SFN   NL            ...           nan            nan            nan 
     1                    2006-01-01   aardsda01        CHN   NL            ...           nan            nan            nan 
     2                    2007-01-01   aardsda01        CHA   AL            ...           nan            nan            nan 
     3                    2008-01-01   aardsda01        BOS   AL            ...           nan            nan            nan 
     4                    2009-01-01   aardsda01        SEA   AL            ...             0            nan              0 
                                 ...         ...        ...   ...                          ...            ...            ...
137970                    1910-01-01   zwilldu01        CHA   AL            ...           nan            nan            nan 
137971                    1914-01-01   zwilldu01        CHF   FL            ...           nan            nan            nan 
137972                    1915-01-01   zwilldu01        CHF   FL            ...           nan            nan            nan 
137973                    1915-01-01   zwilldu01        CHF   FL            ...           nan            nan            nan 
137974                    1916-01-01   zwilldu01        CHN   NL            ...           nan            nan            nan 

  name             CS             ZR
  role   unused_float   unused_float
  unit                              
     0           nan            nan 
     1           nan            nan 
     2           nan            nan 
     3           nan            nan 
     4             0            nan 
                  ...            ...
137970           nan            nan 
137971           nan            nan 
137972           nan            nan 
137973           nan            nan 
137974           nan            nan 


137975 rows x 19 columns
memory usage: 18.76 MB
name: fielding
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/fielding/

In [21]:
fieldingpost["year"] = fieldingpost["yearID"].as_str().as_ts(["%Y"])

fieldingpost.set_role(["playerID", "teamID"], getml.data.roles.join_key)
fieldingpost.set_role(["G", "GS", "InnOuts", "PO", "A", "E", "DP", "TP", "SB", "CS"], getml.data.roles.numerical)
fieldingpost.set_role(fieldingpost.roles.unused_string, getml.data.roles.categorical)
fieldingpost.set_role("year", getml.data.roles.time_stamp)

fieldingpost

name                          year    playerID     teamID   lgID          ...          TP          SB          CS
 role                    time_stamp    join_key   join_key   categorical   ...   numerical   numerical   numerical
 unit   time stamp, comparison only                                        ...                                    
    0                    1957-01-01   aaronha01        ML1   NL            ...           0        nan         nan 
    1                    1958-01-01   aaronha01        ML1   NL            ...           0        nan         nan 
    2                    1958-01-01   aaronha01        ML1   NL            ...           0        nan         nan 
    3                    1969-01-01   aaronha01        ATL   NL            ...           0        nan         nan 
    4                    1979-01-01    aasedo01        CAL   AL            ...           0          0           0 
                                ...         ...        ...   ...                       ...         ...         ...
10341                    2006-01-01    zitoba01        OAK   AL            ...           0          0           1 
10342                    2012-01-01    zitoba01        SFN   NL            ...           0          0           0 
10343                    2012-01-01    zitoba01        SFN   NL            ...           0          0           0 
10344                    2012-01-01    zitoba01        SFN   NL            ...           0          0           0 
10345                    1946-01-01   zuberbi01        BOS   AL            ...           0          0           0 

 name         yearID             PB
 role   unused_float   unused_float
 unit                              
    0           1957           nan 
    1           1958           nan 
    2           1958           nan 
    3           1969           nan 
    4           1979           nan 
                 ...            ...
10341           2006           nan 
10342           2012             0 
10343           2012             0 
10344           2012             0 
10345           1946           nan 


10346 rows x 18 columns
memory usage: 1.28 MB
name: fieldingpost
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/fieldingpost/

In [22]:
pitching["year"] = pitching["yearID"].as_str().as_ts(["%Y"])

pitching.set_role(["playerID", "teamID"], getml.data.roles.join_key)
pitching.set_role([
    "stint", 
    "W", 
    "L", 
    "G", 
    "GS", 
    "CG", 
    "SHO", 
    "SV", 
    "IPouts", 
    "H", 
    "ER", 
    "HR", 
    "BB", 
    "SO", 
    "BAOpp", 
    "ERA", 
    "IBB", 
    "WP", 
    "HBP", 
    "BK", 
    "BFP", 
    "GF", 
    "R"], getml.data.roles.numerical)
pitching.set_role(pitching.roles.unused_string, getml.data.roles.categorical)
pitching.set_role("yearID", getml.data.roles.unused_float)
pitching.set_role("year", getml.data.roles.time_stamp)


pitching

name                          year    playerID     teamID   lgID          ...           R             SH             SF
 role                    time_stamp    join_key   join_key   categorical   ...   numerical   unused_float   unused_float
 unit   time stamp, comparison only                                        ...                                          
    0                    2004-01-01   aardsda01        SFN   NL            ...           8           nan            nan 
    1                    2006-01-01   aardsda01        CHN   NL            ...          25           nan            nan 
    2                    2007-01-01   aardsda01        CHA   AL            ...          24           nan            nan 
    3                    2008-01-01   aardsda01        BOS   AL            ...          32           nan            nan 
    4                    2009-01-01   aardsda01        SEA   AL            ...          23           nan            nan 
                                ...         ...        ...   ...                       ...            ...            ...
39356                    1955-01-01   zuverge01        BAL   AL            ...          28           nan            nan 
39357                    1956-01-01   zuverge01        BAL   AL            ...          52           nan            nan 
39358                    1957-01-01   zuverge01        BAL   AL            ...          37           nan            nan 
39359                    1958-01-01   zuverge01        BAL   AL            ...          29           nan            nan 
39360                    1959-01-01   zuverge01        BAL   AL            ...           7           nan            nan 

 name           GIDP         yearID
 role   unused_float   unused_float
 unit                              
    0           nan            2004
    1           nan            2006
    2           nan            2007
    3           nan            2008
    4           nan            2009
                 ...            ...
39356           nan            1955
39357           nan            1956
39358           nan            1957
39359           nan            1958
39360           nan            1959


39361 rows x 31 columns
memory usage: 9.29 MB
name: pitching
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/pitching/

In [23]:
pitchingpost["year"] = pitchingpost["yearID"].as_str().as_ts(["%Y"])

pitchingpost.set_role(["playerID", "teamID"], getml.data.roles.join_key)
pitchingpost.set_role(pitchingpost.roles.unused_float, getml.data.roles.numerical)
pitchingpost.set_role(pitchingpost.roles.unused_string, getml.data.roles.categorical)
pitchingpost.set_role("yearID", getml.data.roles.unused_float)
pitchingpost.set_role("year", getml.data.roles.time_stamp)

pitchingpost

name                          year    playerID     teamID   round         ...           R          SH          SF        GIDP
role                    time_stamp    join_key   join_key   categorical   ...   numerical   numerical   numerical   numerical
unit   time stamp, comparison only                                        ...                                                
   0                    1979-01-01    aasedo01        CAL   ALCS          ...           1          0           1            0
   1                    1975-01-01   abbotgl01        OAK   ALCS          ...           0          0           0            0
   2                    2000-01-01   abbotpa01        SEA   ALCS          ...           3          0           0            0
   3                    2000-01-01   abbotpa01        SEA   ALDS2         ...           2          0           1            1
   4                    2001-01-01   abbotpa01        SEA   ALCS          ...           0          1           0            0
                               ...         ...        ...   ...                       ...         ...         ...         ...
4192                    2006-01-01    zitoba01        OAK   ALDS2         ...           1          1           0            0
4193                    2012-01-01    zitoba01        SFN   NLCS          ...           0        nan         nan            1
4194                    2012-01-01    zitoba01        SFN   NLDS2         ...           2        nan         nan            0
4195                    2012-01-01    zitoba01        SFN   WS            ...           1        nan         nan            1
4196                    1946-01-01   zuberbi01        BOS   WS            ...           1          0           0            1

name         yearID
role   unused_float
unit               
   0           1979
   1           1975
   2           2000
   3           2000
   4           2001
                ...
4192           2006
4193           2012
4194           2012
4195           2012
4196           1946


4197 rows x 31 columns
memory usage: 0.97 MB
name: pitchingpost
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/pitchingpost/

In [24]:
salaries["year"] = salaries["yearID"].as_str().as_ts(["%Y"])
salaries["teamIDCat"] = salaries["teamID"]

salaries.set_role(["playerID", "teamID"], getml.data.roles.join_key)
salaries.set_role(["lgID", "teamIDCat"], getml.data.roles.categorical)
salaries.set_role("yearID", getml.data.roles.numerical)
salaries.set_role("salary", getml.data.roles.target)
salaries.set_role("year", getml.data.roles.time_stamp)

salaries

name                          year    playerID     teamID     salary   lgID          teamIDCat        yearID
 role                    time_stamp    join_key   join_key     target   categorical   categorical   numerical
 unit   time stamp, comparison only                                                                          
    0                    1985-01-01   barkele01        ATL     870000   NL            ATL                1985
    1                    1985-01-01   bedrost01        ATL     550000   NL            ATL                1985
    2                    1985-01-01   benedbr01        ATL     545000   NL            ATL                1985
    3                    1985-01-01    campri01        ATL     633333   NL            ATL                1985
    4                    1985-01-01   ceronri01        ATL     625000   NL            ATL                1985
                                ...         ...        ...        ...   ...           ...                 ...
23106                    2012-01-01   tracych01        WAS     750000   NL            WAS                2012
23107                    2012-01-01    wangch01        WAS    4000000   NL            WAS                2012
23108                    2012-01-01   werthja01        WAS   13571428   NL            WAS                2012
23109                    2012-01-01   zimmejo02        WAS    2300000   NL            WAS                2012
23110                    2012-01-01   zimmery01        WAS   12000000   NL            WAS                2012


23111 rows x 7 columns
memory usage: 0.92 MB
name: salaries
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/salaries/

## 2. Predictive modeling

We loaded the data and defined the roles and units. Next, we create a getML pipeline for relational learning.

In [25]:
split = getml.data.split.random(train=0.8, test=0.2)

### 2.1 Define relational model

In [26]:
star_schema = getml.data.StarSchema(population=salaries, split=split)

star_schema.join(
    allstarfull,
    on="playerID",
    time_stamps="year",
    horizon=getml.data.time.days(1),
)

star_schema.join(
    awardsplayers,
    on="playerID",
    time_stamps="year",
    horizon=getml.data.time.days(1),
)

star_schema.join(
    awardsshareplayers,
    on="playerID",
    time_stamps="year",
    horizon=getml.data.time.days(1),
)

star_schema.join(
    batting,
    on="playerID",
    time_stamps="year",
    horizon=getml.data.time.days(1),
)

star_schema.join(
    battingpost,
    on="playerID",
    time_stamps="year",
    horizon=getml.data.time.days(1),
)

star_schema.join(
    fielding,
    on="playerID",
    time_stamps="year",
    horizon=getml.data.time.days(1),
)

star_schema.join(
    fieldingpost,
    on="playerID",
    time_stamps="year",
    horizon=getml.data.time.days(1),
)

star_schema.join(
    pitching,
    on="playerID",
    time_stamps="year",
    horizon=getml.data.time.days(1),
)

star_schema.join(
    pitchingpost,
    on="playerID",
    time_stamps="year",
    horizon=getml.data.time.days(1),
)

star_schema

data model

  salaries:
    columns:
    - lgID: categorical
    - teamIDCat: categorical
    - playerID: join_key
    - teamID: join_key
    - yearID: numerical
    - ...

    joins:
    - right: 'allstarfull'
      on: (salaries.playerID, allstarfull.playerID)
      time_stamps: (salaries.year, allstarfull.year)
      relationship: 'many-to-many'
      horizon: 86400.0
      lagged_targets: False
    - right: 'awardsplayers'
      on: (salaries.playerID, awardsplayers.playerID)
      time_stamps: (salaries.year, awardsplayers.year)
      relationship: 'many-to-many'
      horizon: 86400.0
      lagged_targets: False
    - right: 'awardsshareplayers'
      on: (salaries.playerID, awardsshareplayers.playerID)
      time_stamps: (salaries.year, awardsshareplayers.year)
      relationship: 'many-to-many'
      horizon: 86400.0
      lagged_targets: False
    - right: 'batting'
      on: (salaries.playerID, batting.playerID)
      time_stamps: (salaries.year, batting.year)
      relationship: 'many-to-many'
      horizon: 86400.0
      lagged_targets: False
    - right: 'battingpost'
      on: (salaries.playerID, battingpost.playerID)
      time_stamps: (salaries.year, battingpost.year)
      relationship: 'many-to-many'
      horizon: 86400.0
      lagged_targets: False
    - right: 'fielding'
      on: (salaries.playerID, fielding.playerID)
      time_stamps: (salaries.year, fielding.year)
      relationship: 'many-to-many'
      horizon: 86400.0
      lagged_targets: False
    - right: 'fieldingpost'
      on: (salaries.playerID, fieldingpost.playerID)
      time_stamps: (salaries.year, fieldingpost.year)
      relationship: 'many-to-many'
      horizon: 86400.0
      lagged_targets: False
    - right: 'pitching'
      on: (salaries.playerID, pitching.playerID)
      time_stamps: (salaries.year, pitching.year)
      relationship: 'many-to-many'
      horizon: 86400.0
      lagged_targets: False
    - right: 'pitchingpost'
      on: (salaries.playerID, pitchingpost.playerID)
      time_stamps: (salaries.year, pitchingpost.year)
      relationship: 'many-to-many'
      horizon: 86400.0
      lagged_targets: False

  allstarfull:
    columns:
    - gameID: categorical
    - teamID: categorical
    - lgID: categorical
    - playerID: join_key
    - gameNum: numerical
    - ...

  awardsplayers:
    columns:
    - awardID: categorical
    - lgID: categorical
    - notes: categorical
    - playerID: join_key
    - year: time_stamp
    - ...

  awardsshareplayers:
    columns:
    - awardID: categorical
    - lgID: categorical
    - playerID: join_key
    - pointsWon: numerical
    - pointsMax: numerical
    - ...

  batting:
    columns:
    - lgID: categorical
    - playerID: join_key
    - teamID: join_key
    - stint: numerical
    - G: numerical
    - ...

  battingpost:
    columns:
    - round: categorical
    - lgID: categorical
    - playerID: join_key
    - teamID: join_key
    - G: numerical
    - ...

  fielding:
    columns:
    - lgID: categorical
    - POS: categorical
    - playerID: join_key
    - teamID: join_key
    - stint: numerical
    - ...

  fieldingpost:
    columns:
    - lgID: categorical
    - round: categorical
    - POS: categorical
    - playerID: join_key
    - teamID: join_key
    - ...

  pitching:
    columns:
    - lgID: categorical
    - playerID: join_key
    - teamID: join_key
    - stint: numerical
    - W: numerical
    - ...

  pitchingpost:
    columns:
    - round: categorical
    - lgID: categorical
    - playerID: join_key
    - teamID: join_key
    - W: numerical
    - ...


container

  population
      subset   name        rows   type
  0   test     salaries    4539   View
  1   train    salaries   18572   View

  peripheral
      name                   rows   type     
  0   allstarfull            4831   DataFrame
  1   awardsplayers          5795   DataFrame
  2   awardsshareplayers     6289   DataFrame
  3   batting               92353   DataFrame
  4   battingpost            9798 

### 2.2 getML pipeline

<!-- #### 2.1.1  -->
__Set-up the feature learner & predictor__

In [27]:
mapping = getml.preprocessors.Mapping()

fast_prop = getml.feature_learning.FastProp(
    loss_function=getml.feature_learning.loss_functions.SquareLoss,
    num_threads=1,
    num_features=700,
)

relboost = getml.feature_learning.Relboost(
    loss_function=getml.feature_learning.loss_functions.SquareLoss,
    num_threads=1,
    max_depth=8,
)

predictor = getml.predictors.XGBoostRegressor(n_jobs=1)

__Build the pipeline__

In [28]:
pipe1 = getml.pipeline.Pipeline(
    tags=['fast_prop'],
    data_model=star_schema.data_model,
    preprocessors=[mapping],
    feature_learners=[fast_prop],
    predictors=[predictor],
    include_categorical=True,
)

pipe1

Pipeline(data_model='salaries',
         feature_learners=['FastProp'],
         feature_selectors=[],
         include_categorical=True,
         loss_function=None,
         peripheral=['allstarfull', 'awardsplayers', 'awardsshareplayers', 'batting',
                     'battingpost', 'fielding', 'fieldingpost', 'pitching', 'pitchingpost'],
         predictors=['XGBoostRegressor'],
         preprocessors=['Mapping'],
         share_selected_features=0.5,
         tags=['fast_prop'])

In [29]:
pipe2 = getml.pipeline.Pipeline(
    tags=['relboost'],
    data_model=star_schema.data_model,
    preprocessors=[mapping],
    feature_learners=[relboost],
    predictors=[predictor],    
    include_categorical=True,
)

pipe2

Pipeline(data_model='salaries',
         feature_learners=['Relboost'],
         feature_selectors=[],
         include_categorical=True,
         loss_function=None,
         peripheral=['allstarfull', 'awardsplayers', 'awardsshareplayers', 'batting',
                     'battingpost', 'fielding', 'fieldingpost', 'pitching', 'pitchingpost'],
         predictors=['XGBoostRegressor'],
         preprocessors=['Mapping'],
         share_selected_features=0.5,
         tags=['relboost'])

### 2.3 Model training

In [30]:
pipe1.check(star_schema.train)

Checking data model...


Staging...
[========================================] 100%

Preprocessing...
[========================================] 100%

Checking...
[========================================] 100%


INFO [FOREIGN KEYS NOT FOUND]: When joining SALARIES__STAGING_TABLE_1 and ALLSTARFULL__STAGING_TABLE_2 over 'playerID' and 'playerID', there are no corresponding entries for 64.710317% of entries in 'playerID' in 'SALARIES__STAGING_TABLE_1'. You might want to double-check your join keys.
INFO [FOREIGN KEYS NOT FOUND]: When joining SALARIES__STAGING_TABLE_1 and AWARDSPLAYERS__STAGING_TABLE_3 over 'playerID' and 'playerID', there are no corresponding entries for 75.376911% of entries in 'playerID' in 'SALARIES__STAGING_TABLE_1'. You might want to double-check your join keys.
INFO [FOREIGN KEYS NOT FOUND]: When joining SALARIES__STAGING_TABLE_1 and AWARDSSHAREPLAYERS__STAGING_TABLE_4 over 'playerID' and 'playerID', there are no corresponding entries for 62.459617% of entries in '

In [31]:
pipe1.fit(star_schema.train)

Checking data model...


Staging...
[========================================] 100%


INFO [FOREIGN KEYS NOT FOUND]: When joining SALARIES__STAGING_TABLE_1 and ALLSTARFULL__STAGING_TABLE_2 over 'playerID' and 'playerID', there are no corresponding entries for 64.710317% of entries in 'playerID' in 'SALARIES__STAGING_TABLE_1'. You might want to double-check your join keys.
INFO [FOREIGN KEYS NOT FOUND]: When joining SALARIES__STAGING_TABLE_1 and AWARDSPLAYERS__STAGING_TABLE_3 over 'playerID' and 'playerID', there are no corresponding entries for 75.376911% of entries in 'playerID' in 'SALARIES__STAGING_TABLE_1'. You might want to double-check your join keys.
INFO [FOREIGN KEYS NOT FOUND]: When joining SALARIES__STAGING_TABLE_1 and AWARDSSHAREPLAYERS__STAGING_TABLE_4 over 'playerID' and 'playerID', there are no corresponding entries for 62.459617% of entries in 'playerID' in 'SALARIES__STAGING_TABLE_1'. You might want to double-check your join keys.
INFO [FOREIGN KEYS NOT FOUND]: When jo

Pipeline(data_model='salaries',
         feature_learners=['FastProp'],
         feature_selectors=[],
         include_categorical=True,
         loss_function=None,
         peripheral=['allstarfull', 'awardsplayers', 'awardsshareplayers', 'batting',
                     'battingpost', 'fielding', 'fieldingpost', 'pitching', 'pitchingpost'],
         predictors=['XGBoostRegressor'],
         preprocessors=['Mapping'],
         share_selected_features=0.5,
         tags=['fast_prop', 'container-UElAMw'])

url: http://localhost:1709/#/getpipeline/baseball/paxfBX/0/

In [32]:
pipe2.check(star_schema.train)

Checking data model...


Staging...
[========================================] 100%

Preprocessing...
[========================================] 100%

Checking...
[========================================] 100%


INFO [FOREIGN KEYS NOT FOUND]: When joining SALARIES__STAGING_TABLE_1 and ALLSTARFULL__STAGING_TABLE_2 over 'playerID' and 'playerID', there are no corresponding entries for 64.710317% of entries in 'playerID' in 'SALARIES__STAGING_TABLE_1'. You might want to double-check your join keys.
INFO [FOREIGN KEYS NOT FOUND]: When joining SALARIES__STAGING_TABLE_1 and AWARDSPLAYERS__STAGING_TABLE_3 over 'playerID' and 'playerID', there are no corresponding entries for 75.376911% of entries in 'playerID' in 'SALARIES__STAGING_TABLE_1'. You might want to double-check your join keys.
INFO [FOREIGN KEYS NOT FOUND]: When joining SALARIES__STAGING_TABLE_1 and AWARDSSHAREPLAYERS__STAGING_TABLE_4 over 'playerID' and 'playerID', there are no corresponding entries for 62.459617% of entries in '

In [33]:
pipe2.fit(star_schema.train)

Checking data model...


Staging...
[========================================] 100%


INFO [FOREIGN KEYS NOT FOUND]: When joining SALARIES__STAGING_TABLE_1 and ALLSTARFULL__STAGING_TABLE_2 over 'playerID' and 'playerID', there are no corresponding entries for 64.710317% of entries in 'playerID' in 'SALARIES__STAGING_TABLE_1'. You might want to double-check your join keys.
INFO [FOREIGN KEYS NOT FOUND]: When joining SALARIES__STAGING_TABLE_1 and AWARDSPLAYERS__STAGING_TABLE_3 over 'playerID' and 'playerID', there are no corresponding entries for 75.376911% of entries in 'playerID' in 'SALARIES__STAGING_TABLE_1'. You might want to double-check your join keys.
INFO [FOREIGN KEYS NOT FOUND]: When joining SALARIES__STAGING_TABLE_1 and AWARDSSHAREPLAYERS__STAGING_TABLE_4 over 'playerID' and 'playerID', there are no corresponding entries for 62.459617% of entries in 'playerID' in 'SALARIES__STAGING_TABLE_1'. You might want to double-check your join keys.
INFO [FOREIGN KEYS NOT FOUND]: When jo

Pipeline(data_model='salaries',
         feature_learners=['Relboost'],
         feature_selectors=[],
         include_categorical=True,
         loss_function=None,
         peripheral=['allstarfull', 'awardsplayers', 'awardsshareplayers', 'batting',
                     'battingpost', 'fielding', 'fieldingpost', 'pitching', 'pitchingpost'],
         predictors=['XGBoostRegressor'],
         preprocessors=['Mapping'],
         share_selected_features=0.5,
         tags=['relboost', 'container-UElAMw'])

url: http://localhost:1709/#/getpipeline/baseball/5GHzgH/0/

### 2.4 Model evaluation

In [34]:
pipe1.score(star_schema.test)



Staging...
[========================================] 100%

Preprocessing...
[========================================] 100%

FastProp: Building features...
[========================================] 100%




date time             set used   target            mae            rmse   rsquared
0   2021-08-23 17:31:34   train      salary    693195.9259    1251354.7389     0.8222
1   2021-08-23 17:35:07   test       salary    765292.5538    1402960.9382     0.788

In [35]:
pipe2.score(star_schema.test)



Staging...
[========================================] 100%

Preprocessing...
[========================================] 100%

Relboost: Building features...
[========================================] 100%




date time             set used   target            mae            rmse   rsquared
0   2021-08-23 17:34:57   train      salary    461650.4723     798183.2366     0.9276
1   2021-08-23 17:35:13   test       salary    668857.0513    1229058.3492     0.8371

### 2.5 featuretools

In [36]:
population_train_pd = star_schema.train.population.to_pandas()
population_test_pd = star_schema.test.population.to_pandas()

In [37]:
allstarfull_pd = allstarfull.drop(allstarfull.roles.unused).to_pandas()
awardsplayers_pd = awardsplayers.drop(awardsplayers.roles.unused).to_pandas()
awardsshareplayers_pd = awardsshareplayers.drop(awardsshareplayers.roles.unused).to_pandas()
batting_pd = batting.drop(batting.roles.unused).to_pandas()
battingpost_pd = battingpost.drop(battingpost.roles.unused).to_pandas()
fielding_pd = fielding.drop(fielding.roles.unused).to_pandas()
fieldingpost_pd = fieldingpost.drop(fieldingpost.roles.unused).to_pandas()
pitching_pd = pitching.drop(pitching.roles.unused).to_pandas()
pitchingpost_pd = pitchingpost.drop(pitchingpost.roles.unused).to_pandas()

featuretools requires that we manually define a primary key and then join on that primary key. Therefore, we need some manual data preparation.

In [38]:
population_train_pd["id"] = population_train_pd.index
population_train_pd

year   playerID teamID      salary lgID teamIDCat  yearID     id
0     1985-01-01  barkele01    ATL    870000.0   NL       ATL  1985.0      0
1     1985-01-01  bedrost01    ATL    550000.0   NL       ATL  1985.0      1
2     1985-01-01  benedbr01    ATL    545000.0   NL       ATL  1985.0      2
3     1985-01-01  ceronri01    ATL    625000.0   NL       ATL  1985.0      3
4     1985-01-01  chambch01    ATL    800000.0   NL       ATL  1985.0      4
...          ...        ...    ...         ...  ...       ...     ...    ...
18567 2012-01-01  strasst01    WAS   4875000.0   NL       WAS  2012.0  18567
18568 2012-01-01  tracych01    WAS    750000.0   NL       WAS  2012.0  18568
18569 2012-01-01   wangch01    WAS   4000000.0   NL       WAS  2012.0  18569
18570 2012-01-01  werthja01    WAS  13571428.0   NL       WAS  2012.0  18570
18571 2012-01-01  zimmery01    WAS  12000000.0   NL       WAS  2012.0  18571

[18572 rows x 8 columns]

In [39]:
population_test_pd["id"] = population_test_pd.index
population_test_pd

year   playerID teamID     salary lgID teamIDCat  yearID    id
0    1985-01-01   campri01    ATL   633333.0   NL       ATL  1985.0     0
1    1985-01-01  dedmoje01    ATL   150000.0   NL       ATL  1985.0     1
2    1985-01-01  hornebo01    ATL  1500000.0   NL       ATL  1985.0     2
3    1985-01-01  dempsri01    BAL   512500.0   AL       BAL  1985.0     3
4    1985-01-01  martide01    BAL   560000.0   AL       BAL  1985.0     4
...         ...        ...    ...        ...  ...       ...     ...   ...
4534 2012-01-01  desmoia01    WAS   512500.0   NL       WAS  2012.0  4534
4535 2012-01-01  espinda01    WAS   506000.0   NL       WAS  2012.0  4535
4536 2012-01-01  gorzeto01    WAS  3000000.0   NL       WAS  2012.0  4536
4537 2012-01-01  matthry01    WAS   481000.0   NL       WAS  2012.0  4537
4538 2012-01-01  zimmejo02    WAS  2300000.0   NL       WAS  2012.0  4538

[4539 rows x 8 columns]

In [40]:
def prepare_peripheral(peripheral_pd, train_or_test):
    """
    Helper function that imitates the behavior of 
    the data model defined above.
    """
    peripheral_new = peripheral_pd.merge(
        train_or_test[["id", "playerID", "year"]],
        on="playerID"
    )

    peripheral_new = peripheral_new[
        peripheral_new["year_x"] < peripheral_new["year_y"]
    ]

    del peripheral_new["year_x"]
    del peripheral_new["year_y"]
    del peripheral_new["playerID"]

    return peripheral_new

In [41]:
allstarfull_train_pd = prepare_peripheral(allstarfull_pd, population_train_pd)
allstarfull_test_pd = prepare_peripheral(allstarfull_pd, population_test_pd)
allstarfull_train_pd

gameID teamID lgID  gameNum   GP  startingPos     id
1      NLS198607150    BAL   AL      0.0  1.0          NaN   1051
2      NLS198607150    BAL   AL      0.0  1.0          NaN   1569
3      NLS198607150    BAL   AL      0.0  1.0          NaN   2426
11     NLS200407130    PHI   NL      0.0  1.0          NaN  13684
12     NLS200407130    PHI   NL      0.0  1.0          NaN  14357
...             ...    ...  ...      ...  ...          ...    ...
20490  NLS200607110    OAK   AL      0.0  1.0          NaN  17789
20491  NLS200607110    OAK   AL      0.0  1.0          NaN  18456
20494  NLS200907140    TBA   AL      0.0  1.0          NaN  17158
20495  NLS200907140    TBA   AL      0.0  1.0          NaN  17836
20496  NLS200907140    TBA   AL      0.0  1.0          NaN  18502

[11557 rows x 7 columns]

In [42]:
awardsplayers_train_pd = prepare_peripheral(awardsplayers_pd, population_train_pd)
awardsplayers_test_pd = prepare_peripheral(awardsplayers_pd, population_test_pd)
awardsplayers_train_pd

awardID lgID notes     id
0      TSN Player of the Year   AL  NULL   4683
1      TSN Player of the Year   AL  NULL   5856
2      TSN Player of the Year   AL  NULL   8922
3      TSN Player of the Year   AL  NULL   9727
4          Rookie of the Year   NL  NULL    120
...                       ...  ...   ...    ...
26203        Hank Aaron Award   AL  NULL  18529
26209          Silver Slugger   AL    OF  18529
26213                NLCS MVP   NL  NULL  17779
26228  Roberto Clemente Award   ML  NULL  17310
26245                ALCS MVP   AL  NULL  18506

[15639 rows x 4 columns]

In [43]:
awardsshareplayers_train_pd = prepare_peripheral(awardsshareplayers_pd, population_train_pd)
awardsshareplayers_test_pd = prepare_peripheral(awardsshareplayers_pd, population_test_pd)
awardsshareplayers_train_pd

awardID lgID  pointsWon  pointsMax  votesFirst     id
0                Cy Young   NL        1.0       24.0         1.0    254
1                Cy Young   NL        1.0       24.0         1.0    614
2                Cy Young   NL       15.0      120.0         1.0    254
3                Cy Young   NL       15.0      120.0         1.0    614
4                Cy Young   NL       10.0      120.0         0.0    254
...                   ...  ...        ...        ...         ...    ...
24216  Rookie of the Year   AL        3.0      140.0         0.0  16986
24217  Rookie of the Year   AL        3.0      140.0         0.0  18315
24218  Rookie of the Year   NL        9.0      160.0         0.0  16703
24219  Rookie of the Year   NL        9.0      160.0         0.0  17370
24220  Rookie of the Year   NL        9.0      160.0         0.0  18404

[15527 rows x 6 columns]

In [44]:
batting_train_pd = prepare_peripheral(batting_pd, population_train_pd)
batting_test_pd = prepare_peripheral(batting_pd, population_test_pd)
batting_train_pd

teamID lgID  stint     G  G_batting     AB     R     H   2B   3B  ...  \
1         SFN   NL    1.0  11.0       11.0    0.0   0.0   0.0  0.0  0.0  ...   
2         SFN   NL    1.0  11.0       11.0    0.0   0.0   0.0  0.0  0.0  ...   
3         SFN   NL    1.0  11.0       11.0    0.0   0.0   0.0  0.0  0.0  ...   
4         SFN   NL    1.0  11.0       11.0    0.0   0.0   0.0  0.0  0.0  ...   
5         SFN   NL    1.0  11.0       11.0    0.0   0.0   0.0  0.0  0.0  ...   
...       ...  ...    ...   ...        ...    ...   ...   ...  ...  ...  ...   
208118    ATL   NL    1.0  11.0       11.0   25.0   2.0   5.0  1.0  0.0  ...   
208119    ATL   NL    1.0  81.0       81.0  190.0  16.0  48.0  8.0  1.0  ...   
208120    NYA   AL    1.0  21.0       21.0   48.0   2.0   4.0  1.0  0.0  ...   
208121    NYA   AL    1.0  14.0       14.0   34.0   2.0   6.0  0.0  0.0  ...   
208122    CLE   AL    1.0  51.0       51.0  130.0   9.0  30.0  5.0  1.0  ...   

         CS    BB    SO  IBB  HBP   SH   SF  GIDP  G_old     id  
1       0.0   0.0   0.0  0.0  0.0  0.0  0.0   0.0   11.0  14656  
2       0.0   0.0   0.0  0.0  0.0  0.0  0.0   0.0   11.0  16389  
3       0.0   0.0   0.0  0.0  0.0  0.0  0.0   0.0   11.0  17069  
4       0.0   0.0   0.0  0.0  0.0  0.0  0.0   0.0   11.0  17743  
5       0.0   0.0   0.0  0.0  0.0  0.0  0.0   0.0   11.0  18263  
...     ...   ...   ...  ...  ...  ...  ...   ...    ...    ...  
208118  0.0   2.0   3.0  0.0  0.0  0.0  0.0   0.0   11.0   2109  
208119  0.0  16.0  14.0  1.0  0.0  4.0  0.0   3.0   81.0   2109  
208120  0.0   5.0   4.0  0.0  0.0  4.0  0.0   1.0   21.0   2109  
208121  0.0   0.0   4.0  0.0  0.0  2.0  0.0   1.0   14.0   2109  
208122  0.0   8.0  13.0  0.0  0.0  8.0  0.0   3.0   51.0   2109  

[105808 rows x 23 columns]

In [45]:
battingpost_train_pd = prepare_peripheral(battingpost_pd, population_train_pd)
battingpost_test_pd = prepare_peripheral(battingpost_pd, population_test_pd)
battingpost_train_pd

teamID  round lgID    G   AB    R    H   2B   3B   HR  ...   SB   CS  \
0        SLN     WS   NL  1.0  1.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
1        SLN     WS   NL  1.0  1.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
2        SLN     WS   NL  2.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
3        SLN     WS   NL  2.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
4        PHI   NLCS   NL  1.0  2.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
...      ...    ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
49525    ARI  NLDS2   NL  3.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
49530    ARI  NLDS2   NL  1.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
49544    TEX     WS   AL  3.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
49549    TEX     WS   AL  3.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
49566    TEX     WS   AL  2.0  5.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   

        BB   SO  IBB  HBP   SH   SF  GIDP     id  
0      0.0  0.0  0.0  0.0  0.0  0.0   0.0    301  
1      0.0  0.0  0.0  0.0  0.0  0.0   0.0    533  
2      0.0  0.0  0.0  0.0  0.0  0.0   0.0    301  
3      0.0  0.0  0.0  0.0  0.0  0.0   0.0    533  
4      0.0  0.0  0.0  0.0  0.0  0.0   0.0    301  
...    ...  ...  ...  ...  ...  ...   ...    ...  
49525  0.0  0.0  NaN  NaN  NaN  NaN   NaN  17924  
49530  1.0  0.0  NaN  NaN  NaN  NaN   NaN  17926  
49544  0.0  0.0  NaN  NaN  NaN  NaN   NaN  18503  
49549  0.0  0.0  NaN  NaN  NaN  NaN   NaN  18508  
49566  0.0  2.0  NaN  NaN  NaN  NaN   NaN  18516  

[22893 rows x 21 columns]

In [46]:
fielding_train_pd = prepare_peripheral(fielding_pd, population_train_pd)
fielding_test_pd = prepare_peripheral(fielding_pd, population_test_pd)
fielding_train_pd

teamID lgID POS  stint     G    GS  InnOuts    PO      A    E    DP  \
1         SFN   NL   P    1.0  11.0   0.0     32.0   0.0    0.0  0.0   0.0   
2         SFN   NL   P    1.0  11.0   0.0     32.0   0.0    0.0  0.0   0.0   
3         SFN   NL   P    1.0  11.0   0.0     32.0   0.0    0.0  0.0   0.0   
4         SFN   NL   P    1.0  11.0   0.0     32.0   0.0    0.0  0.0   0.0   
5         SFN   NL   P    1.0  11.0   0.0     32.0   0.0    0.0  0.0   0.0   
...       ...  ...  ..    ...   ...   ...      ...   ...    ...  ...   ...   
361010    NYA   AL  SS    1.0  21.0  18.0    453.0  30.0   54.0  3.0  12.0   
361011    NYA   AL  2B    1.0   7.0   6.0    168.0  17.0   18.0  0.0   5.0   
361012    NYA   AL  3B    1.0   1.0   0.0      3.0   0.0    0.0  0.0   0.0   
361013    NYA   AL  SS    1.0   6.0   1.0     70.0   3.0    7.0  0.0   0.0   
361014    CLE   AL  SS    1.0  49.0  44.0   1139.0  77.0  112.0  8.0  21.0   

           id  
1       14656  
2       16389  
3       17069  
4       17743  
5       18263  
...       ...  
361010   2109  
361011   2109  
361012   2109  
361013   2109  
361014   2109  

[182144 rows x 12 columns]

In [47]:
fieldingpost_train_pd = prepare_peripheral(fieldingpost_pd, population_train_pd)
fieldingpost_test_pd = prepare_peripheral(fieldingpost_pd, population_test_pd)
fieldingpost_train_pd

teamID lgID  round POS    G   GS  InnOuts   PO    A    E   DP   TP   SB  \
0        CAL   AL   ALCS   P  2.0  0.0     15.0  0.0  1.0  0.0  0.0  0.0  0.0   
1        CAL   AL   ALCS   P  2.0  0.0     15.0  0.0  1.0  0.0  0.0  0.0  0.0   
2        CAL   AL   ALCS   P  2.0  0.0     15.0  0.0  1.0  0.0  0.0  0.0  0.0   
3        CAL   AL   ALCS   P  2.0  0.0     15.0  0.0  1.0  0.0  0.0  0.0  0.0   
11       FLO   NL   NLCS  2B  2.0  2.0     51.0  4.0  1.0  0.0  0.0  0.0  NaN   
...      ...  ...    ...  ..  ...  ...      ...  ...  ...  ...  ...  ...  ...   
58087    OAK   AL   ALCS   P  1.0  1.0     11.0  0.0  2.0  0.0  0.0  0.0  0.0   
58088    OAK   AL   ALCS   P  1.0  1.0     11.0  0.0  2.0  0.0  0.0  0.0  0.0   
58095    OAK   AL  ALDS2   P  1.0  1.0     24.0  0.0  1.0  0.0  0.0  0.0  0.0   
58096    OAK   AL  ALDS2   P  1.0  1.0     24.0  0.0  1.0  0.0  0.0  0.0  0.0   
58097    OAK   AL  ALDS2   P  1.0  1.0     24.0  0.0  1.0  0.0  0.0  0.0  0.0   

        CS     id  
0      0.0    454  
1      0.0   1051  
2      0.0   1569  
3      0.0   2426  
11     NaN   8818  
...    ...    ...  
58087  0.0  17789  
58088  0.0  18456  
58095  1.0  17114  
58096  1.0  17789  
58097  1.0  18456  

[27491 rows x 15 columns]

In [48]:
pitching_train_pd = prepare_peripheral(pitching_pd, population_train_pd)
pitching_test_pd = prepare_peripheral(pitching_pd, population_test_pd)
pitching_train_pd

teamID lgID  stint     W     L     G    GS   CG  SHO   SV  ...  BAOpp  \
1        SFN   NL    1.0   1.0   0.0  11.0   0.0  0.0  0.0  0.0  ...    0.0   
2        SFN   NL    1.0   1.0   0.0  11.0   0.0  0.0  0.0  0.0  ...    0.0   
3        SFN   NL    1.0   1.0   0.0  11.0   0.0  0.0  0.0  0.0  ...    0.0   
4        SFN   NL    1.0   1.0   0.0  11.0   0.0  0.0  0.0  0.0  ...    0.0   
5        SFN   NL    1.0   1.0   0.0  11.0   0.0  0.0  0.0  0.0  ...    0.0   
...      ...  ...    ...   ...   ...   ...   ...  ...  ...  ...  ...    ...   
91802    SFN   NL    1.0  10.0  13.0  33.0  33.0  1.0  0.0  0.0  ...    NaN   
91803    SFN   NL    1.0  10.0  13.0  33.0  33.0  1.0  0.0  0.0  ...    NaN   
91811    SFN   NL    1.0   9.0  14.0  34.0  33.0  1.0  0.0  0.0  ...    NaN   
91812    SFN   NL    1.0   9.0  14.0  34.0  33.0  1.0  0.0  0.0  ...    NaN   
91821    SFN   NL    1.0   3.0   4.0  13.0   9.0  0.0  0.0  0.0  ...    NaN   

       ERA  IBB   WP  HBP   BK    BFP   GF     R     id  
1      6.0  0.0  0.0  2.0  0.0   61.0  5.0   8.0  14656  
2      6.0  0.0  0.0  2.0  0.0   61.0  5.0   8.0  16389  
3      6.0  0.0  0.0  2.0  0.0   61.0  5.0   8.0  17069  
4      6.0  0.0  0.0  2.0  0.0   61.0  5.0   8.0  17743  
5      6.0  0.0  0.0  2.0  0.0   61.0  5.0   8.0  18263  
...    ...  ...  ...  ...  ...    ...  ...   ...    ...  
91802  4.0  8.0  2.0  8.0  2.0  818.0  0.0  89.0  17789  
91803  4.0  8.0  2.0  8.0  2.0  818.0  0.0  89.0  18456  
91811  4.0  7.0  7.0  7.0  0.0  848.0  1.0  97.0  17789  
91812  4.0  7.0  7.0  7.0  0.0  848.0  1.0  97.0  18456  
91821  5.0  1.0  1.0  0.0  0.0  225.0  3.0  35.0  18456  

[45669 rows x 26 columns]

In [49]:
pitchingpost_train_pd = prepare_peripheral(pitchingpost_pd, population_train_pd)
pitchingpost_test_pd = prepare_peripheral(pitchingpost_pd, population_test_pd)
pitchingpost_train_pd

teamID  round lgID    W    L    G   GS   CG  SHO   SV  ...   WP  HBP  \
0        CAL   ALCS   AL  1.0  0.0  2.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
1        CAL   ALCS   AL  1.0  0.0  2.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
2        CAL   ALCS   AL  1.0  0.0  2.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
3        CAL   ALCS   AL  1.0  0.0  2.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
7        SEA   ALCS   AL  0.0  1.0  1.0  1.0  0.0  0.0  0.0  ...  0.0  0.0   
...      ...    ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
24239    OAK   ALCS   AL  0.0  1.0  1.0  1.0  0.0  0.0  0.0  ...  0.0  0.0   
24240    OAK   ALCS   AL  0.0  1.0  1.0  1.0  0.0  0.0  0.0  ...  0.0  0.0   
24247    OAK  ALDS2   AL  1.0  0.0  1.0  1.0  0.0  0.0  0.0  ...  0.0  0.0   
24248    OAK  ALDS2   AL  1.0  0.0  1.0  1.0  0.0  0.0  0.0  ...  0.0  0.0   
24249    OAK  ALDS2   AL  1.0  0.0  1.0  1.0  0.0  0.0  0.0  ...  0.0  0.0   

        BK   BFP   GF    R   SH   SF  GIDP     id  
0      0.0  20.0  2.0  1.0  0.0  1.0   0.0    454  
1      0.0  20.0  2.0  1.0  0.0  1.0   0.0   1051  
2      0.0  20.0  2.0  1.0  0.0  1.0   0.0   1569  
3      0.0  20.0  2.0  1.0  0.0  1.0   0.0   2426  
7      0.0  21.0  0.0  3.0  0.0  0.0   0.0  11801  
...    ...   ...  ...  ...  ...  ...   ...    ...  
24239  0.0  21.0  0.0  5.0  0.0  0.0   0.0  17789  
24240  0.0  21.0  0.0  5.0  0.0  0.0   0.0  18456  
24247  0.0  30.0  0.0  1.0  1.0  0.0   0.0  17114  
24248  0.0  30.0  0.0  1.0  1.0  0.0   0.0  17789  
24249  0.0  30.0  0.0  1.0  1.0  0.0   0.0  18456  

[11364 rows x 29 columns]

In [50]:
population_train_pd

year   playerID teamID      salary lgID teamIDCat  yearID     id
0     1985-01-01  barkele01    ATL    870000.0   NL       ATL  1985.0      0
1     1985-01-01  bedrost01    ATL    550000.0   NL       ATL  1985.0      1
2     1985-01-01  benedbr01    ATL    545000.0   NL       ATL  1985.0      2
3     1985-01-01  ceronri01    ATL    625000.0   NL       ATL  1985.0      3
4     1985-01-01  chambch01    ATL    800000.0   NL       ATL  1985.0      4
...          ...        ...    ...         ...  ...       ...     ...    ...
18567 2012-01-01  strasst01    WAS   4875000.0   NL       WAS  2012.0  18567
18568 2012-01-01  tracych01    WAS    750000.0   NL       WAS  2012.0  18568
18569 2012-01-01   wangch01    WAS   4000000.0   NL       WAS  2012.0  18569
18570 2012-01-01  werthja01    WAS  13571428.0   NL       WAS  2012.0  18570
18571 2012-01-01  zimmery01    WAS  12000000.0   NL       WAS  2012.0  18571

[18572 rows x 8 columns]

In [51]:
entities_train = {
    "population" : (population_train_pd, "id"),
    "allstarfull": (allstarfull_train_pd, "index"),
    "awardsplayers": (awardsplayers_train_pd, "index"),
    "awardsshareplayers": (awardsshareplayers_train_pd, "index"),
    "batting": (batting_train_pd, "index"),
    "battingpost": (battingpost_train_pd, "index"),
    "fielding": (fielding_train_pd, "index"),
    "fieldingpost": (fieldingpost_train_pd, "index"),
    "pitching": (pitching_train_pd, "index"),
    "pitchingpost": (pitchingpost_train_pd, "index"),
}

In [52]:
entities_test = {
    "population" : (population_test_pd, "id"),
    "allstarfull": (allstarfull_test_pd, "index"),
    "awardsplayers": (awardsplayers_test_pd, "index"),
    "awardsshareplayers": (awardsshareplayers_test_pd, "index"),
    "batting": (batting_test_pd, "index"),
    "battingpost": (battingpost_test_pd, "index"),
    "fielding": (fielding_test_pd, "index"),
    "fieldingpost": (fieldingpost_test_pd, "index"),
    "pitching": (pitching_test_pd, "index"),
    "pitchingpost": (pitchingpost_test_pd, "index"),
}

In [53]:
relationships = [
    ("population", "id", "allstarfull", "id"),
    ("population", "id", "awardsplayers", "id"),
    ("population", "id", "awardsshareplayers", "id"),
    ("population", "id", "batting", "id"),
    ("population", "id", "battingpost", "id"),
    ("population", "id", "fielding", "id"),
    ("population", "id", "fieldingpost", "id"),
    ("population", "id", "pitching", "id"),
    ("population", "id", "pitchingpost", "id"),
]

In [54]:
featuretools_train_pd = featuretools.dfs(
    entities=entities_train,
    relationships=relationships,
    target_entity="population")[0]

/home/patrick/.local/lib/python3.9/site-packages/featuretools/entityset/entity.py:462: UserWarning: index index not found in dataframe, creating new integer column
  warnings.warn("index {} not found in dataframe, creating new "


In [55]:
featuretools_test_pd = featuretools.dfs(
    entities=entities_test,
    relationships=relationships,
    target_entity="population")[0]

In [56]:
featuretools_train = getml.data.DataFrame.from_pandas(featuretools_train_pd, "featuretools_train")
featuretools_test = getml.data.DataFrame.from_pandas(featuretools_test_pd, "featuretools_test")

In [57]:
featuretools_train.set_role("salary", getml.data.roles.target)
featuretools_train.set_role(featuretools_train.roles.unused_float, getml.data.roles.numerical)
featuretools_train.set_role(featuretools_train.roles.unused_string, getml.data.roles.categorical)

featuretools_train

91.880250% of all entries of column 'MAX(allstarfull.startingPos)' are NULL values.
91.880250% of all entries of column 'MEAN(allstarfull.startingPos)' are NULL values.
91.880250% of all entries of column 'MIN(allstarfull.startingPos)' are NULL values.
91.923325% of all entries of column 'SKEW(allstarfull.GP)' are NULL values.
91.912557% of all entries of column 'SKEW(allstarfull.gameNum)' are NULL values.
97.571613% of all entries of column 'SKEW(allstarfull.startingPos)' are NULL values.
96.047814% of all entries of column 'STD(allstarfull.startingPos)' are NULL values.
91.158734% of all entries of column 'SKEW(pitchingpost.BAOpp)' are NULL values.
91.142580% of all entries of column 'SKEW(pitchingpost.BB)' are NULL values.
91.142580% of all entries of column 'SKEW(pitchingpost.BFP)' are NULL values.
91.142580% of all entries of column 'SKEW(pitchingpost.BK)' are NULL values.
91.142580% of all entries of column 'SKEW(pitchingpost.CG)' are NULL values.
91.142580% of all entries of col

name     salary   playerID      teamID        lgID          ...   SUM(pitchingpost.WP)   DAY(year)   MONTH(year)
 role     target   categorical   categorical   categorical   ...              numerical   numerical     numerical
    0     870000   barkele01     ATL           NL            ...                      0           1             1
    1     550000   bedrost01     ATL           NL            ...                      1           1             1
    2     545000   benedbr01     ATL           NL            ...                      0           1             1
    3     625000   ceronri01     ATL           NL            ...                      0           1             1
    4     800000   chambch01     ATL           NL            ...                      0           1             1
             ...   ...           ...           ...                                  ...         ...           ...
18567    4875000   strasst01     WAS           NL            ...                      0           1             1
18568     750000   tracych01     WAS           NL            ...                      0           1             1
18569    4000000   wangch01      WAS           NL            ...                      0           1             1
18570   13571428   werthja01     WAS           NL            ...                      0           1             1
18571   12000000   zimmery01     WAS           NL            ...                      0           1             1

 name   WEEKDAY(year)   YEAR(year)
 role       numerical    numerical
    0               1         1985
    1               1         1985
    2               1         1985
    3               1         1985
    4               1         1985
                  ...          ...
18567               6         2012
18568               6         2012
18569               6         2012
18570               6         2012
18571               6         2012


18572 rows x 723 columns
memory usage: 105.27 MB
name: featuretools_train
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/featuretools_train/

In [58]:
featuretools_test.set_role("salary", getml.data.roles.target)
featuretools_test.set_role(featuretools_test.roles.unused_float, getml.data.roles.numerical)
featuretools_test.set_role(featuretools_test.roles.unused_string, getml.data.roles.categorical)

featuretools_test

91.451862% of all entries of column 'MAX(allstarfull.startingPos)' are NULL values.
91.451862% of all entries of column 'MEAN(allstarfull.startingPos)' are NULL values.
91.451862% of all entries of column 'MIN(allstarfull.startingPos)' are NULL values.
91.914519% of all entries of column 'SKEW(allstarfull.GP)' are NULL values.
91.892487% of all entries of column 'SKEW(allstarfull.gameNum)' are NULL values.
97.884997% of all entries of column 'SKEW(allstarfull.startingPos)' are NULL values.
96.342807% of all entries of column 'STD(allstarfull.startingPos)' are NULL values.
90.746861% of all entries of column 'SKEW(pitchingpost.BAOpp)' are NULL values.
90.724829% of all entries of column 'SKEW(pitchingpost.BB)' are NULL values.
90.724829% of all entries of column 'SKEW(pitchingpost.BFP)' are NULL values.
90.724829% of all entries of column 'SKEW(pitchingpost.BK)' are NULL values.
90.724829% of all entries of column 'SKEW(pitchingpost.CG)' are NULL values.
90.724829% of all entries of col

name    salary   playerID      teamID        lgID          ...   SUM(pitchingpost.WP)   DAY(year)   MONTH(year)
role    target   categorical   categorical   categorical   ...              numerical   numerical     numerical
   0    633333   campri01      ATL           NL            ...                      0           1             1
   1    150000   dedmoje01     ATL           NL            ...                      0           1             1
   2   1500000   hornebo01     ATL           NL            ...                      0           1             1
   3    512500   dempsri01     BAL           AL            ...                      0           1             1
   4    560000   martide01     BAL           AL            ...                      0           1             1
           ...   ...           ...           ...                                  ...         ...           ...
4534    512500   desmoia01     WAS           NL            ...                      0           1             1
4535    506000   espinda01     WAS           NL            ...                      0           1             1
4536   3000000   gorzeto01     WAS           NL            ...                      0           1             1
4537    481000   matthry01     WAS           NL            ...                      0           1             1
4538   2300000   zimmejo02     WAS           NL            ...                      0           1             1

name   WEEKDAY(year)   YEAR(year)
role       numerical    numerical
   0               1         1985
   1               1         1985
   2               1         1985
   3               1         1985
   4               1         1985
                 ...          ...
4534               6         2012
4535               6         2012
4536               6         2012
4537               6         2012
4538               6         2012


4539 rows x 723 columns
memory usage: 25.73 MB
name: featuretools_test
type: getml.DataFrame
url: http://localhost:1709/#/getdataframe/baseball/featuretools_test/

We train an untuned XGBoostRegressor on top of featuretools' features, just like we have done for getML's features.

Since some of featuretools features are categorical, we allow the pipeline to include these features as well. Other features contain NaN values, which is why we also apply getML's Imputation preprocessor.

In [59]:
imputation = getml.preprocessors.Imputation()

predictor = getml.predictors.XGBoostRegressor(n_jobs=1)

pipe3 = getml.pipeline.Pipeline(
    tags=['featuretools'],
    preprocessors=[imputation],
    predictors=[predictor],
    include_categorical=True,
)

pipe3

Pipeline(data_model='population',
         feature_learners=[],
         feature_selectors=[],
         include_categorical=True,
         loss_function=None,
         peripheral=[],
         predictors=['XGBoostRegressor'],
         preprocessors=['Imputation'],
         share_selected_features=0.5,
         tags=['featuretools'])

In [60]:
pipe3.fit(featuretools_train)

Checking data model...


Staging...
[========================================] 100%

Preprocessing...
[========================================] 100%

Checking...
[========================================] 100%


INFO [MIGHT TAKE LONG]: The number of unique entries in column 'playerid' in POPULATION__STAGING_TABLE_1 is 4272. This might take a long time to fit. You should consider setting its role to unused_string or using it for comparison only (you can do the latter by setting a unit that contains 'comparison only').
WARNING [COLUMN SHOULD BE UNUSED]: All non-NULL entries in column 'COALESCE( max(allstarfull.gamenum), 0.000000 )' in POPULATION__STAGING_TABLE_1 are equal to each other. You should consider setting its role to unused_float or using it for comparison only (you can do the latter by setting a unit that contains 'comparison only').
WARNING [COLUMN SHOULD BE UNUSED]: All non-NULL entries in column 'COALESCE( mean(allstarfull.gamenum), 0.000000 )' in POPULATION__STAGING_TABLE_

Pipeline(data_model='population',
         feature_learners=[],
         feature_selectors=[],
         include_categorical=True,
         loss_function=None,
         peripheral=[],
         predictors=['XGBoostRegressor'],
         preprocessors=['Imputation'],
         share_selected_features=0.5,
         tags=['featuretools'])

url: http://localhost:1709/#/getpipeline/baseball/7FaFcm/0/

In [61]:
pipe3.score(featuretools_test)



Staging...
[========================================] 100%

Preprocessing...
[========================================] 100%




date time             set used             target            mae            rmse   rsquared
0   2021-08-23 17:42:04   featuretools_train   salary    703972.7245    1283939.7829     0.8144
1   2021-08-23 17:42:07   featuretools_test    salary    769939.416     1431516.0502     0.7797

### 2.6 Productionization

It is possible to productionize the pipeline by transpiling the features into production-ready SQL code. Please also refer to getML's `sqlite3` module.

In [62]:
# Creates a folder named baseball_pipeline containing
# the SQL code.
pipe2.features.to_sql().save("baseball_pipeline")

### 2.7 Discussion

For a more convenient overview, we summarize our results into a table.

Name                 | R-squared  | RMSE      | MAE
-------------------- | ---------- | ----------| ----
getML: FastProp      |     78.80% | 1,402,960 | 765,292
getML: Relboost      |     83.95% | 1,220,382 | 666,548
featuretools         |     77.97% | 1,431,516 | 769,939

As we can see, Relboost outperforms FastProp and both algorithms outperform featuretools according to all three measures.

## 3. Conclusion

We have demonstrated how statistical relational learning can be used for sabermetrics. We have also shown that getML outperforms featuretools on this dataset.

## References

Motl, Jan, and Oliver Schulte. "The CTU prague relational learning repository." arXiv preprint arXiv:1511.03086 (2015).

# Next Steps

This tutorial benchmarked getML against academic state-of-the-art algorithms from relational learning literature and getML's qualities with respect to categorical data.

If you are interested in further real-world applications of getML, head back to the [notebook overview](welcome.md) and choose one of the remaining examples.

Here is some additional material from our [documentation](https://docs.getml.com/latest/) if you want to learn more about getML:
* [Feature learning with Multirel](https://docs.getml.com/latest/user_guide/feature_engineering/feature_engineering.html#multirel)
* [Feature learning with Relboost](https://docs.getml.com/latest/user_guide/feature_engineering/feature_engineering.html#relboost)

# Get in contact

If you have any question schedule a [call with Alex](https://go.getml.com/meetings/alexander-uhlig/getml-demo), the co-founder of getML, or write us an [email](team@getml.com). Prefer a private demo of getML? Just contact us to make an appointment.